<a href="https://colab.research.google.com/github/Ignas12345/Magistro_projektas/blob/main/knygutes/TCGA_isoformu_atsisiuntimas.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
if (!requireNamespace("BiocManager", quietly = TRUE))
    install.packages("BiocManager")

Installing package into ‘/usr/local/lib/R/site-library’
(as ‘lib’ is unspecified)



In [2]:
BiocManager::install("TCGAbiolinks", ask = FALSE, verbose = TRUE)

'getOption("repos")' replaces Bioconductor standard repositories, see
'help("repositories", package = "BiocManager")' for details.
Replacement repositories:
    CRAN: https://cran.rstudio.com

Bioconductor version 3.20 (BiocManager 1.30.25), R 4.4.2 (2024-10-31)

Installing package(s) 'BiocVersion', 'TCGAbiolinks'

system (cmd0): /usr/lib/R/bin/R CMD INSTALL

also installing the dependencies ‘plogr’, ‘png’, ‘Biostrings’, ‘RSQLite’, ‘KEGGREST’, ‘filelock’, ‘UCSC.utils’, ‘GenomeInfoDbData’, ‘zlibbioc’, ‘matrixStats’, ‘abind’, ‘SparseArray’, ‘AnnotationDbi’, ‘BiocFileCache’, ‘BiocGenerics’, ‘GenomeInfoDb’, ‘XVector’, ‘R.oo’, ‘R.methodsS3’, ‘MatrixGenerics’, ‘Biobase’, ‘S4Arrays’, ‘DelayedArray’, ‘downloader’, ‘biomaRt’, ‘GenomicRanges’, ‘XML’, ‘plyr’, ‘IRanges’, ‘S4Vectors’, ‘R.utils’, ‘SummarizedExperiment’, ‘TCGAbiolinksGUI.data’


foundpkgs: plogr, png, Biostrings, RSQLite, KEGGREST, filelock, UCSC.utils, GenomeInfoDbData, zlibbioc, matrixStats, abind, SparseArray, AnnotationDbi, BiocF

In [51]:
library(TCGAbiolinks)

In [5]:
clinical_data <- GDCquery_clinic(project = "TCGA-TGCT", type = "clinical")

In [6]:
teratoma_submitter_ids <- clinical_data$submitter_id[clinical_data$primary_diagnosis == "Teratoma, benign"]
teratoma_submitter_ids <- teratoma_submitter_ids[!is.na(teratoma_submitter_ids)]

# View the result
teratoma_submitter_ids

[1] "TCGA-2G-AAG5" "TCGA-2G-AAG6" "TCGA-2G-AAGY" "TCGA-2G-AAGV" "TCGA-2G-AAGX"

In [7]:
query_miRNA_1 <- GDCquery(
  project = "TCGA-TGCT",
  data.category = "Transcriptome Profiling",
  data.type = "Isoform Expression Quantification",
  barcode = teratoma_submitter_ids
)

--------------------------------------

o GDCquery: Searching in GDC database

--------------------------------------

Genome of reference: hg38

--------------------------------------------

oo Accessing GDC. This might take a while...

--------------------------------------------

ooo Project: TCGA-TGCT

--------------------

oo Filtering results

--------------------

ooo By data.type

ooo By barcode

----------------

oo Checking data

----------------

ooo Checking if there are duplicated cases

ooo Checking if there are results for the query

-------------------

o Preparing output

-------------------



In [8]:
GDCdownload(query_miRNA_1)

# Prepare the data for analysis



GDCdownload will download 6 files. A total of 3.467809 MB




Downloading: 390 kB     

In [110]:
data_teratoma <- GDCprepare(query_miRNA_1)

  |======================================================================| 100%


In [111]:
head(data_teratoma)

miRNA_ID     isoform_coords                read_count
1 hsa-let-7a-1 hg38:chr9:94175961-94175982:+     5     
2 hsa-let-7a-1 hg38:chr9:94175961-94175983:+    11     
3 hsa-let-7a-1 hg38:chr9:94175961-94175984:+    25     
4 hsa-let-7a-1 hg38:chr9:94175962-94175981:+   210     
5 hsa-let-7a-1 hg38:chr9:94175962-94175982:+  7881     
6 hsa-let-7a-1 hg38:chr9:94175962-94175983:+ 21250     
  reads_per_million_miRNA_mapped cross-mapped miRNA_region       
1    0.427537                    N            mature,MIMAT0000062
2    0.940582                    N            mature,MIMAT0000062
3    2.137686                    N            mature,MIMAT0000062
4   17.956564                    N            mature,MIMAT0000062
5  673.884179                    N            mature,MIMAT0000062
6 1817.033220                    N            mature,MIMAT0000062
  barcode                     
1 TCGA-2G-AAG5-01A-11R-A439-13
2 TCGA-2G-AAG5-01A-11R-A439-13
3 TCGA-2G-AAG5-01A-11R-A439-13
4 TCGA-2G-AAG5-01A-11R-A439-13
5 TCGA-2G-AAG5-01A-11R-A439-13
6 TCGA-2G-AAG5-01A-11R-A439-13

In [50]:
library(dplyr)
library(tidyr)

In [53]:
# Combine miRNA_ID and miRNA_region into a single identifier
data_teratoma <- data_teratoma %>%
  mutate(miRNA_id_and_region = paste(miRNA_ID, miRNA_region, sep = ", "))

# This should be summing the read counts per million RNA mapped, but instead it sums the regular read counts
aggregated_data_teratoma <- data_teratoma %>%
  group_by(miRNA_id_and_region, barcode) %>%
  summarise(total_reads_per_million_miRNA_mapped = sum(reads_per_million_miRNA_mapped), .groups = "drop")

# Reshape into wide format
final_teratoma_reads_per_million_miRNA_mapped <- aggregated_data_teratoma %>%
  pivot_wider(names_from = barcode, values_from = total_reads_per_million_miRNA_mapped, values_fill = 0)

# View the resulting table
head(final_teratoma_reads_per_million_miRNA_mapped, n = 20)

miRNA_id_and_region               TCGA-2G-AAG5-01A-11R-A439-13
1  hsa-let-7a-1, mature,MIMAT0000062  8442.150108                
2  hsa-let-7a-1, mature,MIMAT0004481    12.655100                
3  hsa-let-7a-1, precursor               0.000000                
4  hsa-let-7a-1, stemloop                0.171014                
5  hsa-let-7a-2, mature,MIMAT0000062  8413.761636                
6  hsa-let-7a-2, mature,MIMAT0010195    25.652234                
7  hsa-let-7a-2, precursor               2.223193                
8  hsa-let-7a-2, stemloop                0.171014                
9  hsa-let-7a-3, mature,MIMAT0000062  8481.996578                
10 hsa-let-7a-3, mature,MIMAT0004481    11.543503                
11 hsa-let-7b, mature,MIMAT0000063   12386.523068                
12 hsa-let-7b, mature,MIMAT0004482       8.037699                
13 hsa-let-7b, precursor                 0.085507                
14 hsa-let-7b, stemloop                  0.000000                
15 hsa-let-7c, mature,MIMAT0000064    9098.505257                
16 hsa-let-7c, mature,MIMAT0026472      70.030595                
17 hsa-let-7c, precursor                 0.000000                
18 hsa-let-7c, stemloop                  0.342029                
19 hsa-let-7d, mature,MIMAT0000065     219.497611                
20 hsa-let-7d, mature,MIMAT0004484     469.521382                
   TCGA-2G-AAG6-01A-11R-A439-13 TCGA-2G-AAGV-01A-11R-A439-13
1   9733.713953                  8041.494616                
2      7.216914                     7.132565                
3      0.097526                     0.126240                
4      0.390104                     0.441840                
5   9718.890021                  7995.290739                
6     20.480429                    10.541048                
7      1.267835                     1.388641                
8      0.097526                     0.063120                
9   9859.180961                  8100.448744                
10     6.631759                     7.953125                
11 12561.671083                  6858.183002                
12     7.802068                     3.471603                
13     0.195052                     0.000000                
14     0.000000                     0.000000                
15 15844.293735                 30126.253988                
16    99.232556                   110.460090                
17     0.048763                     0.126240                
18     0.292578                     0.315600                
19   293.406527                    97.268000                
20   282.288579                   118.539456                
   TCGA-2G-AAGX-01A-11R-A439-13 TCGA-2G-AAGY-01A-11R-A439-13
1  14120.154510                 6193.217126                 
2     16.142226                   14.458626                 
3      0.279923                    0.158886                 
4      0.279923                    0.158886                 
5  14156.171267                 6141.420291                 
6     52.718828                   46.076938                 
7      3.452383                    5.719896                 
8      0.000000                    0.000000                 
9  14220.180322                 6207.675752                 
10    15.955609                   17.954118                 
11 17336.562777                 6616.648297                 
12    12.223303                    6.673212                 
13     0.000000                    0.317772                 
14     0.186616                    0.000000                 
15 33838.115321                 9340.113106                 
16   353.822640                  139.501902                 
17     0.000000                    0.000000                 
18     0.559846                    0.000000                 
19   246.892064                  158.409335                 
20   582.333091                  282.022638                 
   TCGA-2G-AAGY-05A-11R-A439-13
1  6483.152667         

In [ ]:
teratoma_reads <- as.data.frame(final_teratoma_reads_per_million_miRNA_mapped[,-1])
rownames(teratoma_reads) <- final_teratoma_reads_per_million_miRNA_mapped$miRNA_id_and_region

In [115]:
head(teratoma_reads, n =10)


TCGA-2G-AAG5-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 8442.150108                 
hsa-let-7a-1, mature,MIMAT0004481   12.655100                 
hsa-let-7a-1, precursor              0.000000                 
hsa-let-7a-1, stemloop               0.171014                 
hsa-let-7a-2, mature,MIMAT0000062 8413.761636                 
hsa-let-7a-2, mature,MIMAT0010195   25.652234                 
hsa-let-7a-2, precursor              2.223193                 
hsa-let-7a-2, stemloop               0.171014                 
hsa-let-7a-3, mature,MIMAT0000062 8481.996578                 
hsa-let-7a-3, mature,MIMAT0004481   11.543503                 
                                  TCGA-2G-AAG6-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 9733.713953                 
hsa-let-7a-1, mature,MIMAT0004481    7.216914                 
hsa-let-7a-1, precursor              0.097526                 
hsa-let-7a-1, stemloop               0.390104                 
hsa-let-7a-2, mature,MIMAT0000062 9718.890021                 
hsa-let-7a-2, mature,MIMAT0010195   20.480429                 
hsa-let-7a-2, precursor              1.267835                 
hsa-let-7a-2, stemloop               0.097526                 
hsa-let-7a-3, mature,MIMAT0000062 9859.180961                 
hsa-let-7a-3, mature,MIMAT0004481    6.631759                 
                                  TCGA-2G-AAGV-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 8041.494616                 
hsa-let-7a-1, mature,MIMAT0004481    7.132565                 
hsa-let-7a-1, precursor              0.126240                 
hsa-let-7a-1, stemloop               0.441840                 
hsa-let-7a-2, mature,MIMAT0000062 7995.290739                 
hsa-let-7a-2, mature,MIMAT0010195   10.541048                 
hsa-let-7a-2, precursor              1.388641                 
hsa-let-7a-2, stemloop               0.063120                 
hsa-let-7a-3, mature,MIMAT0000062 8100.448744                 
hsa-let-7a-3, mature,MIMAT0004481    7.953125                 
                                  TCGA-2G-AAGX-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 14120.154510                
hsa-let-7a-1, mature,MIMAT0004481    16.142226                
hsa-let-7a-1, precursor               0.279923                
hsa-let-7a-1, stemloop                0.279923                
hsa-let-7a-2, mature,MIMAT0000062 14156.171267                
hsa-let-7a-2, mature,MIMAT0010195    52.718828                
hsa-let-7a-2, precursor               3.452383                
hsa-let-7a-2, stemloop                0.000000                
hsa-let-7a-3, mature,MIMAT0000062 14220.180322                
hsa-let-7a-3, mature,MIMAT0004481    15.955609                
                                  TCGA-2G-AAGY-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 6193.217126                 
hsa-let-7a-1, mature,MIMAT0004481   14.458626                 
hsa-let-7a-1, precursor              0.158886                 
hsa-let-7a-1, stemloop               0.158886                 
hsa-let-7a-2, mature,MIMAT0000062 6141.420291                 
hsa-let-7a-2, mature,MIMAT0010195   46.076938                 
hsa-let-7a-2, precursor              5.719896                 
hsa-let-7a-2, stemloop               0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 6207.675752                 
hsa-let-7a-3, mature,MIMAT0004481   17.954118                 
                                  TCGA-2G-AAGY-05A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 6483.152667                 
hsa-let-7a-1, mature,MIMAT0004481    4.028750                 
hsa-let-7a-1, precursor              0.895278                 
hsa-let-7a-1, stemloop               0.000000                 
hsa-let-7a-2, mature,MIMAT0000062 6618.339583                 
hsa-let-7a-2, mature,MIMAT0010195    2.685833                 
hsa-let-7a-2, precursor              0.000000                 
hsa-let-7a-2, stemloop               0.000000                 
hs

In [117]:
print(sum(teratoma_reads$'TCGA-2G-AAG5-01A-11R-A439-13'))

[1] 1e+06


In [55]:
other_submitter_ids <- clinical_data$submitter_id[clinical_data$primary_diagnosis != "Teratoma, benign"]
other_submitter_ids <- other_submitter_ids[!is.na(other_submitter_ids)]

# View the result
other_submitter_ids

[1] "TCGA-2G-AAFE" "TCGA-2G-AAGA" "TCGA-ZM-AA05" "TCGA-2G-AAKD" "TCGA-X3-A8G4"
  [6] "TCGA-2G-AAG7" "TCGA-XE-A8H1" "TCGA-2G-AAF1" "TCGA-2G-AAFL" "TCGA-2G-AAHC"
 [11] "TCGA-ZM-AA0B" "TCGA-XE-A9SE" "TCGA-ZM-AA0E" "TCGA-2G-AAGM" "TCGA-XE-AAO3"
 [16] "TCGA-YU-A94D" "TCGA-XE-AAOC" "TCGA-2G-AAFN" "TCGA-XY-A89B" "TCGA-ZM-AA0F"
 [21] "TCGA-2G-AAL7" "TCGA-2G-AAGZ" "TCGA-SN-A84Y" "TCGA-SN-A84W" "TCGA-XE-AANJ"
 [26] "TCGA-2G-AAHP" "TCGA-2G-AAKL" "TCGA-2G-AAGI" "TCGA-XE-AAO4" "TCGA-YU-A94I"
 [31] "TCGA-XE-A8H5" "TCGA-2G-AAF4" "TCGA-2G-AAFJ" "TCGA-S6-A8JW" "TCGA-ZM-AA06"
 [36] "TCGA-XE-AANV" "TCGA-2G-AAFH" "TCGA-SB-A6J6" "TCGA-VF-A8A9" "TCGA-XE-AAOD"
 [41] "TCGA-2G-AAEW" "TCGA-2G-AAF6" "TCGA-XY-A8S3" "TCGA-2X-A9D5" "TCGA-VF-A8A8"
 [46] "TCGA-YU-AA61" "TCGA-2G-AAFV" "TCGA-2X-A9D6" "TCGA-2G-AAFY" "TCGA-2G-AAGC"
 [51] "TCGA-S6-A8JY" "TCGA-XE-AAOF" "TCGA-W4-A7U2" "TCGA-2G-AAG0" "TCGA-2G-AAEX"
 [56] "TCGA-2G-AAH2" "TCGA-YU-AA4L" "TCGA-4K-AA1H" "TCGA-2G-AAGT" "TCGA-XY-A8S2"
 [61] "TCGA-YU-A90S" "TCGA-2G-AAG9" "TCGA-2G-AAGW" "TCGA-2G-AAL5" "TCGA-2G-AAKG"
 [66] "TCGA-ZM-AA0D" "TCGA-W4-A7U3" "TCGA-YU-A90W" "TCGA-2G-AAGJ" "TCGA-VF-A8AC"
 [71] "TCGA-SN-A84X" "TCGA-4K-AAAL" "TCGA-XE-AAO6" "TCGA-2G-AAGE" "TCGA-2G-AAFG"
 [76] "TCGA-2G-AAGO" "TCGA-2G-AAFO" "TCGA-2G-AAH8" "TCGA-SB-A76C" "TCGA-2G-AAFI"
 [81] "TCGA-SN-A6IS" "TCGA-XE-AAOB" "TCGA-YU-A90Y" "TCGA-WZ-A8D5" "TCGA-2G-AAGF"
 [86] "TCGA-XE-A8H4" "TCGA-2G-AAHT" "TCGA-YU-A90Q" "TCGA-ZM-AA0H" "TCGA-YU-A90P"
 [91] "TCGA-XY-A9T9" "TCGA-2G-AAFM" "TCGA-2G-AAGK" "TCGA-WZ-A7V4" "TCGA-2G-AAGS"
 [96] "TCGA-2G-AAKM" "TCGA-XE-AAOL" "TCGA-YU-A912" "TCGA-2G-AAGN" "TCGA-2G-AAG3"
[101] "TCGA-2G-AAF8" "TCGA-VF-A8AA" "TCGA-2G-AAHL" "TCGA-2G-AAGG" "TCGA-W4-A7U4"
[106] "TCGA-VF-A8AD" "TCGA-XE-AANI" "TCGA-2G-AALP" "TCGA-2G-AAKH" "TCGA-WZ-A7V5"
[111] "TCGA-2G-AAHN" "TCGA-2G-AAG8" "TCGA-VF-A8AE" "TCGA-2G-AAHA" "TCGA-2G-AAH0"
[116] "TCGA-2G-AAH4" "TCGA-4K-AA1G" "TCGA-VF-A8AB" "TCGA-ZM-AA0N" "TCGA-WZ-A7V3"
[121] "TCGA-2G-AAH3" "TCGA-4K-AA1I" "TCGA-S6-A8JX" "TCGA-SO-A8JP" "TCGA-2G-AAFZ"
[126] "TCGA-XE-AANR" "TCGA-XE-AAOJ" "TCGA-2G-AAHG" "TCGA-2G-AAGP" "TCGA-2G-AAL6"
[131] "TCGA-2G-AAH7" "TCGA-2G-AAIH" "TCGA-XE-AANS" "TCGA-2G-AAHW" "TCGA-YU-AA60"
[136] "TCGA-XE-A8GZ" "TCGA-2G-AAEZ" "TCGA-2G-AAII" "TCGA-2G-AAG2" "TCGA-2G-AAEV"
[141] "TCGA-2G-AAIF" "TCGA-2G-AAHU" "TCGA-2G-AAHD" "TCGA-XE-AANZ" "TCGA-2G-AAH9"
[146] "TCGA-2G-AAL4" "TCGA-XE-AAO9" "TCGA-2G-AAI8" "TCGA-2G-AAI7" "TCGA-2G-AAG4"
[151] "TCGA-YU-A90V" "TCGA-2G-AAHZ" "TCGA-YU-A94N" "TCGA-2G-AAGB" "TCGA-2G-AAF3"
[156] "TCGA-XE-A8H0" "TCGA-2G-AAHM" "TCGA-XE-AAOH" "TCGA-2G-AAIC" "TCGA-XE-AAO5"
[161] "TCGA-2G-AAF2" "TCGA-2G-AAKQ" "TCGA-XE-AANX" "TCGA-XE-AAOM" "TCGA-2G-AAHR"
[166] "TCGA-2G-AAHB" "TCGA-XE-AANN" "TCGA-2G-AAI5" "TCGA-2G-AAKF" "TCGA-2G-AAIG"
[171] "TCGA-YU-A90R" "TCGA-YU-A90Z" "TCGA-YU-A94C" "TCGA-2G-AAFF" "TCGA-XE-AAO0"
[176] "TCGA-2G-AAFC" "TCGA-XE-AANQ" "TCGA-2G-AAH5" "TCGA-2G-AAK7" "TCGA-2G-AAHI"
[181] "TCGA-2G-AAFW" "TCGA-2G-AAF9" "TCGA-2G-AAHJ" "TCGA-2G-AAES" "TCGA-2G-AAFR"
[186] "TCGA-XE-AAOE" "TCGA-YU-A94A" "TCGA-XE-AAO7" "TCGA-2G-AAKJ" "TCGA-2G-AAKK"
[191] "TCGA-XE-AAOQ" "TCGA-2G-AAHF" "TCGA-2G-AAIE" "TCGA-2G-AAFD" "TCGA-2G-AAI6"
[196] "TCGA-2G-AAFA" "TCGA-YU-A94J" "TCGA-2G-AAF0" "TCGA-2G-AAFX" "TCGA-XE-AANF"
[201] "TCGA-2G-AAER" "TCGA-2G-AAHK" "TCGA-XE-AANH" "TCGA-2G-AAGR" "TCGA-XE-AANU"
[206] "TCGA-XE-AANB" "TCGA-2G-AAIA" "TCGA-2G-AAG1" "TCGA-2G-AAFB" "TCGA-XE-AANM"
[211] "TCGA-2G-AAID" "TCGA-2G-AAI4" "TCGA-2G-AAGU" "TCGA-2G-AAIB" "TCGA-2G-AAHH"
[216] "TCGA-2G-AALC" "TCGA-2G-AAHO" "TCGA-2G-AAEY" "TCGA-XE-AANK" "TCGA-YU-A94M"
[221] "TCGA-2G-AAHY" "TCGA-2G-AAET" "TCGA-2G-AAI3" "TCGA-XE-AAOI" "TCGA-2G-AAFU"
[226] "TCGA-YU-A948" "TCGA-2G-AAL8" "TCGA-2G-AAHV" "TCGA-YU-A94K" "TCGA-2G-AAI2"
[231] "TCGA-YU-A94L" "TCGA-2G-AAF7" "TCGA-XE-AAOO" "TCGA-2G-AAEQ" "TCGA-2G-AAGL"
[236] "TCGA-2G-AAEU" "TCGA-2G-AAHE" "TCGA-YU-A94H" "TCGA-2G-AAGQ" "TCGA-YU-A94B"
[241] "TCGA-2G-AAI9" "TCGA-XE-AAND"

In [56]:
query_miRNA_2 <- GDCquery(
  project = "TCGA-TGCT",
  data.category = "Transcriptome Profiling",
  data.type = "Isoform Expression Quantification",
  barcode = other_submitter_ids
)

--------------------------------------

o GDCquery: Searching in GDC database

--------------------------------------

Genome of reference: hg38

--------------------------------------------

oo Accessing GDC. This might take a while...

--------------------------------------------

ooo Project: TCGA-TGCT

--------------------

oo Filtering results

--------------------

ooo By data.type

ooo By barcode

----------------

oo Checking data

----------------

ooo Checking if there are duplicated cases

ooo Checking if there are results for the query

-------------------

o Preparing output

-------------------



In [57]:
GDCdownload(query_miRNA_2)



GDCdownload will download 133 files. A total of 72.845722 MB




Downloading: 8.1 MB     

In [113]:
data_other <- GDCprepare(query_miRNA_2)

  |======================================================================| 100%


In [59]:
# Combine miRNA_ID and miRNA_region into a single identifier
data_other <- data_other %>%
  mutate(miRNA_id_and_region = paste(miRNA_ID, miRNA_region, sep = ", "))

# This should be summing the read counts per million RNA mapped, but instead it sums the regular read counts
aggregated_data_other <- data_other %>%
  group_by(miRNA_id_and_region, barcode) %>%
  summarise(total_reads_per_million_miRNA_mapped = sum(reads_per_million_miRNA_mapped), .groups = "drop")

# Reshape into wide format
final_other_reads_per_million_miRNA_mapped <- aggregated_data_other %>%
  pivot_wider(names_from = barcode, values_from = total_reads_per_million_miRNA_mapped, values_fill = 0)

# View the resulting table
head(final_other_reads_per_million_miRNA_mapped, n = 20)

miRNA_id_and_region               TCGA-2G-AAEW-01A-11R-A439-13
1  hsa-let-7a-1, mature,MIMAT0000062 6619.132919                 
2  hsa-let-7a-1, mature,MIMAT0004481    4.294653                 
3  hsa-let-7a-1, precursor              0.671040                 
4  hsa-let-7a-1, stemloop               0.000000                 
5  hsa-let-7a-2, mature,MIMAT0000062 6651.745435                 
6  hsa-let-7a-2, mature,MIMAT0010195    1.744703                 
7  hsa-let-7a-2, precursor              0.268416                 
8  hsa-let-7a-2, stemloop               0.000000                 
9  hsa-let-7a-3, mature,MIMAT0000062 6705.697005                 
10 hsa-let-7a-3, mature,MIMAT0004481    2.952574                 
11 hsa-let-7a-3, stemloop               0.000000                 
12 hsa-let-7b, mature,MIMAT0000063   7813.180477                 
13 hsa-let-7b, mature,MIMAT0004482      6.039356                 
14 hsa-let-7b, precursor                0.000000                 
15 hsa-let-7b, stemloop                 0.000000                 
16 hsa-let-7b, unannotated              0.000000                 
17 hsa-let-7c, mature,MIMAT0000064    746.866884                 
18 hsa-let-7c, mature,MIMAT0026472      1.073664                 
19 hsa-let-7c, precursor                0.000000                 
20 hsa-let-7c, stemloop                 0.000000                 
   TCGA-2G-AAEX-01A-11R-A439-13 TCGA-2G-AAF1-01A-11R-A439-13
1   7412.830012                 7711.910036                 
2      3.647631                    5.938329                 
3      0.561174                    0.304530                 
4      0.000000                    0.000000                 
5   7454.356898                 7686.786336                 
6      2.525284                    1.370384                 
7      0.280587                    0.304530                 
8      0.000000                    0.000000                 
9   7577.254039                 7678.259505                 
10     4.489393                    6.395124                 
11     0.000000                    0.000000                 
12 13315.820957                 9467.980531                 
13     9.259374                    5.633799                 
14     0.280587                    0.152265                 
15     0.000000                    0.000000                 
16     0.000000                    0.000000                 
17  1939.417883                 1024.133369                 
18     7.295263                    4.415681                 
19     0.000000                    0.000000                 
20     0.000000                    0.000000                 
   TCGA-2G-AAF4-01A-11R-A439-13 TCGA-2G-AAF6-01A-11R-A439-13
1  6090.723837                  8102.343665                 
2     6.816354                     6.972757                 
3     0.929503                     0.410162                 
4     0.000000                     0.000000                 
5  6134.410483                  8174.122047                 
6     3.408178                     0.820324                 
7     0.929503                     0.000000                 
8     0.000000                     0.000000                 
9  6136.269488                  8188.477724                 
10    6.196687                     9.023568                 
11    0.000000                     0.000000                 
12 8300.462489                  6135.616023                 
13    7.436024                     6.972757                 
14    0.309834                     0.000000                 
15    0.000000                     0.000000                 
16    0.000000                     0.000000                 
17 1273.419216                   977.416468                 
18    7.745859                     4.101622                 
19    0.000000                     0.000000                 
20    0.000000                     0.000000                 
   TCGA-2G-AAF8-01A-11R-A439-13 TCGA-2G-AAFE-01A-11R-A4

In [88]:
other_reads <- as.data.frame(final_other_reads_per_million_miRNA_mapped[,-1])
rownames(other_reads) <- final_other_reads_per_million_miRNA_mapped$miRNA_id_and_region

In [118]:
print(nrow(final_other_reads_per_million_miRNA_mapped))

[1] 3599


In [119]:
print(nrow(other_reads))

[1] 3599


In [108]:
teratoma_reads[grepl('371', rownames(teratoma_reads)),]

TCGA-2G-AAG5-01A-11R-A439-13
hsa-mir-371a, mature,MIMAT0000723 1.197103                    
hsa-mir-371a, mature,MIMAT0004687 1.966672                    
hsa-mir-371a, precursor           0.000000                    
hsa-mir-371a, stemloop            0.000000                    
hsa-mir-371b, mature,MIMAT0019892 0.000000                    
hsa-mir-6735, mature,MIMAT0027371 0.085507                    
                                  TCGA-2G-AAG6-01A-11R-A439-13
hsa-mir-371a, mature,MIMAT0000723  7.460729                   
hsa-mir-371a, mature,MIMAT0004687 10.874133                   
hsa-mir-371a, precursor            0.000000                   
hsa-mir-371a, stemloop             0.000000                   
hsa-mir-371b, mature,MIMAT0019892  0.000000                   
hsa-mir-6735, mature,MIMAT0027371  0.048763                   
                                  TCGA-2G-AAGV-01A-11R-A439-13
hsa-mir-371a, mature,MIMAT0000723 1.199281                    
hsa-mir-371a, mature,MIMAT0004687 1.956721                    
hsa-mir-371a, precursor           0.000000                    
hsa-mir-371a, stemloop            0.000000                    
hsa-mir-371b, mature,MIMAT0019892 0.000000                    
hsa-mir-6735, mature,MIMAT0027371 0.378720                    
                                  TCGA-2G-AAGX-01A-11R-A439-13
hsa-mir-371a, mature,MIMAT0000723 168.980169                  
hsa-mir-371a, mature,MIMAT0004687 299.610888                  
hsa-mir-371a, precursor             0.093308                  
hsa-mir-371a, stemloop              0.279923                  
hsa-mir-371b, mature,MIMAT0019892   0.000000                  
hsa-mir-6735, mature,MIMAT0027371   0.186616                  
                                  TCGA-2G-AAGY-01A-11R-A439-13
hsa-mir-371a, mature,MIMAT0000723  8.262072                   
hsa-mir-371a, mature,MIMAT0004687 11.122020                   
hsa-mir-371a, precursor            0.000000                   
hsa-mir-371a, stemloop             0.000000                   
hsa-mir-371b, mature,MIMAT0019892  0.000000                   
hsa-mir-6735, mature,MIMAT0027371  0.158886                   
                                  TCGA-2G-AAGY-05A-11R-A439-13
hsa-mir-371a, mature,MIMAT0000723 4685.882905                 
hsa-mir-371a, mature,MIMAT0004687 4625.451668                 
hsa-mir-371a, precursor              2.685834                 
hsa-mir-371a, stemloop               0.895278                 
hsa-mir-371b, mature,MIMAT0019892    0.447639                 
hsa-mir-6735, mature,MIMAT0027371    0.447639

In [120]:
other_reads[grepl('371', rownames(other_reads)),]

TCGA-2G-AAEW-01A-11R-A439-13
hsa-mir-3714, mature,MIMAT0018165      0.000000                 
hsa-mir-371a, mature,MIMAT0000723   1502.859905                 
hsa-mir-371a, mature,MIMAT0004687   1995.402844                 
hsa-mir-371a, precursor                0.402624                 
hsa-mir-371a, stemloop                 0.000000                 
hsa-mir-371b, mature,MIMAT0019892      0.000000                 
hsa-mir-371b, mature,MIMAT0019893      0.000000                 
hsa-mir-6087, mature,MIMAT0023712      0.000000                 
hsa-mir-6089-1, mature,MIMAT0023714    0.000000                 
hsa-mir-6735, mature,MIMAT0027371      0.134208                 
                                    TCGA-2G-AAEX-01A-11R-A439-13
hsa-mir-3714, mature,MIMAT0018165      0.000000                 
hsa-mir-371a, mature,MIMAT0000723   2454.575758                 
hsa-mir-371a, mature,MIMAT0004687   3452.343408                 
hsa-mir-371a, precursor                3.647632                 
hsa-mir-371a, stemloop                 0.280587                 
hsa-mir-371b, mature,MIMAT0019892      0.000000                 
hsa-mir-371b, mature,MIMAT0019893      0.280587                 
hsa-mir-6087, mature,MIMAT0023712      0.000000                 
hsa-mir-6089-1, mature,MIMAT0023714    0.000000                 
hsa-mir-6735, mature,MIMAT0027371      0.280587                 
                                    TCGA-2G-AAF1-01A-11R-A439-13
hsa-mir-3714, mature,MIMAT0018165      0.000000                 
hsa-mir-371a, mature,MIMAT0000723   1518.841862                 
hsa-mir-371a, mature,MIMAT0004687   2036.846877                 
hsa-mir-371a, precursor                0.000000                 
hsa-mir-371a, stemloop                 0.152265                 
hsa-mir-371b, mature,MIMAT0019892      0.000000                 
hsa-mir-371b, mature,MIMAT0019893      0.000000                 
hsa-mir-6087, mature,MIMAT0023712      0.000000                 
hsa-mir-6089-1, mature,MIMAT0023714    0.000000                 
hsa-mir-6735, mature,MIMAT0027371      0.152265                 
                                    TCGA-2G-AAF4-01A-11R-A439-13
hsa-mir-3714, mature,MIMAT0018165      0.000000                 
hsa-mir-371a, mature,MIMAT0000723   2540.022078                 
hsa-mir-371a, mature,MIMAT0004687   2150.560290                 
hsa-mir-371a, precursor                4.647514                 
hsa-mir-371a, stemloop                 1.859006                 
hsa-mir-371b, mature,MIMAT0019892      0.000000                 
hsa-mir-371b, mature,MIMAT0019893      0.000000                 
hsa-mir-6087, mature,MIMAT0023712      0.000000                 
hsa-mir-6089-1, mature,MIMAT0023714    0.000000                 
hsa-mir-6735, mature,MIMAT0027371      0.929503                 
                                    TCGA-2G-AAF6-01A-11R-A439-13
hsa-mir-3714, mature,MIMAT0018165      0.000000                 
hsa-mir-371a, mature,MIMAT0000723   3661.107598                 
hsa-mir-371a, mature,MIMAT0004687   3691.049440                 
hsa-mir-371a, precursor                3.281297                 
hsa-mir-371a, stemloop                 0.000000                 
hsa-mir-371b, mature,MIMAT0019892      0.000000                 
hsa-mir-371b, mature,MIMAT0019893      0.000000                 
hsa-mir-6087, mature,MIMAT0023712      0.000000                 
hsa-mir-6089-1, mature,MIMAT0023714    0.000000                 
hsa-mir-6735, mature,MIMAT0027371      0.410162                 
                                    TCGA-2G-AAF8-01A-11R-A439-13
hsa-mir-3714, mature,MIMAT0018165      0.000000                 
hsa-mir-371a, mature,MIMAT0000723   5581.460884                 
hsa-mir-371a, mature,MIMAT0004687   5707.643453                 
hsa-mir-371a, precursor                8.917497                 
hsa-mir-371a, stemloop                 0.000000                 
hsa-mir-371b, mature,MIMAT0019892      0.000000                 
hsa-mi

In [121]:
filtered_teratoma = teratoma_reads[(rowSums(teratoma_reads[])>1*ncol(teratoma_reads)),]
print(nrow(filtered_teratoma))

[1] 801


In [122]:
filtered_other = other_reads[(rowSums(other_reads[])>1*ncol(other_reads)),]
print(nrow(filtered_other))

[1] 947


In [128]:
#sujungiam naudodami chat GPT koda...

# Find the union of row names
all_rows <- union(rownames(filtered_teratoma), rownames(filtered_other))

# Reindex filtered_teratoma to include all rows, fill missing rows with 0
filtered_teratoma_full <- data.frame(matrix(0, nrow = length(all_rows), ncol = ncol(filtered_teratoma)))
rownames(filtered_teratoma_full) <- all_rows
colnames(filtered_teratoma_full) <- colnames(filtered_teratoma)
filtered_teratoma_full[rownames(filtered_teratoma), ] <- filtered_teratoma

# Reindex filtered_other to include all rows, fill missing rows with 0
filtered_other_full <- data.frame(matrix(0, nrow = length(all_rows), ncol = ncol(filtered_other)))
rownames(filtered_other_full) <- all_rows
colnames(filtered_other_full) <- colnames(filtered_other)
filtered_other_full[rownames(filtered_other), ] <- filtered_other

# Combine the two data frames by column
combined_df <- cbind(filtered_teratoma_full, filtered_other_full)

# View the resulting combined data frame
print(combined_df)


                                     TCGA-2G-AAG5-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062                    8.442150e+03
hsa-let-7a-1, mature,MIMAT0004481                    1.265510e+01
hsa-let-7a-2, mature,MIMAT0000062                    8.413762e+03
hsa-let-7a-2, mature,MIMAT0010195                    2.565223e+01
hsa-let-7a-2, precursor                              2.223193e+00
hsa-let-7a-3, mature,MIMAT0000062                    8.481997e+03
hsa-let-7a-3, mature,MIMAT0004481                    1.154350e+01
hsa-let-7b, mature,MIMAT0000063                      1.238652e+04
hsa-let-7b, mature,MIMAT0004482                      8.037699e+00
hsa-let-7c, mature,MIMAT0000064                      9.098505e+03
hsa-let-7c, mature,MIMAT0026472                      7.003059e+01
hsa-let-7d, mature,MIMAT0000065                      2.194976e+02
hsa-let-7d, mature,MIMAT0004484                      4.695214e+02
hsa-let-7e, mature,MIMAT0000066                      2.105450e+03
hsa-let-7e

In [132]:
head(other_reads, n= 20)

TCGA-2G-AAEW-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 6619.132919                 
hsa-let-7a-1, mature,MIMAT0004481    4.294653                 
hsa-let-7a-1, precursor              0.671040                 
hsa-let-7a-1, stemloop               0.000000                 
hsa-let-7a-2, mature,MIMAT0000062 6651.745435                 
hsa-let-7a-2, mature,MIMAT0010195    1.744703                 
hsa-let-7a-2, precursor              0.268416                 
hsa-let-7a-2, stemloop               0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 6705.697005                 
hsa-let-7a-3, mature,MIMAT0004481    2.952574                 
hsa-let-7a-3, stemloop               0.000000                 
hsa-let-7b, mature,MIMAT0000063   7813.180477                 
hsa-let-7b, mature,MIMAT0004482      6.039356                 
hsa-let-7b, precursor                0.000000                 
hsa-let-7b, stemloop                 0.000000                 
hsa-let-7b, unannotated              0.000000                 
hsa-let-7c, mature,MIMAT0000064    746.866884                 
hsa-let-7c, mature,MIMAT0026472      1.073664                 
hsa-let-7c, precursor                0.000000                 
hsa-let-7c, stemloop                 0.000000                 
                                  TCGA-2G-AAEX-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062  7412.830012                
hsa-let-7a-1, mature,MIMAT0004481     3.647631                
hsa-let-7a-1, precursor               0.561174                
hsa-let-7a-1, stemloop                0.000000                
hsa-let-7a-2, mature,MIMAT0000062  7454.356898                
hsa-let-7a-2, mature,MIMAT0010195     2.525284                
hsa-let-7a-2, precursor               0.280587                
hsa-let-7a-2, stemloop                0.000000                
hsa-let-7a-3, mature,MIMAT0000062  7577.254039                
hsa-let-7a-3, mature,MIMAT0004481     4.489393                
hsa-let-7a-3, stemloop                0.000000                
hsa-let-7b, mature,MIMAT0000063   13315.820957                
hsa-let-7b, mature,MIMAT0004482       9.259374                
hsa-let-7b, precursor                 0.280587                
hsa-let-7b, stemloop                  0.000000                
hsa-let-7b, unannotated               0.000000                
hsa-let-7c, mature,MIMAT0000064    1939.417883                
hsa-let-7c, mature,MIMAT0026472       7.295263                
hsa-let-7c, precursor                 0.000000                
hsa-let-7c, stemloop                  0.000000                
                                  TCGA-2G-AAF1-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 7711.910036                 
hsa-let-7a-1, mature,MIMAT0004481    5.938329                 
hsa-let-7a-1, precursor              0.304530                 
hsa-let-7a-1, stemloop               0.000000                 
hsa-let-7a-2, mature,MIMAT0000062 7686.786336                 
hsa-let-7a-2, mature,MIMAT0010195    1.370384                 
hsa-let-7a-2, precursor              0.304530                 
hsa-let-7a-2, stemloop               0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 7678.259505                 
hsa-let-7a-3, mature,MIMAT0004481    6.395124                 
hsa-let-7a-3, stemloop               0.000000                 
hsa-let-7b, mature,MIMAT0000063   9467.980531                 
hsa-let-7b, mature,MIMAT0004482      5.633799                 
hsa-let-7b, precursor                0.152265                 
hsa-let-7b, stemloop                 0.000000                 
hsa-let-7b, unannotated              0.000000                 
hsa-let-7c, mature,MIMAT0000064   1024.133369                 
hsa-let-7c, mature,MIMAT0026472      4.415681                 
hsa-let-7c, precursor                0.000000                 
hsa-let-7c, stemloop                 0.000000                 
                                  TCGA-2G-AAF4-01A-11R-A439-13
hs

In [129]:
head(combined_df)

TCGA-2G-AAG5-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 8442.150108                 
hsa-let-7a-1, mature,MIMAT0004481   12.655100                 
hsa-let-7a-2, mature,MIMAT0000062 8413.761636                 
hsa-let-7a-2, mature,MIMAT0010195   25.652234                 
hsa-let-7a-2, precursor              2.223193                 
hsa-let-7a-3, mature,MIMAT0000062 8481.996578                 
                                  TCGA-2G-AAG6-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 9733.713953                 
hsa-let-7a-1, mature,MIMAT0004481    7.216914                 
hsa-let-7a-2, mature,MIMAT0000062 9718.890021                 
hsa-let-7a-2, mature,MIMAT0010195   20.480429                 
hsa-let-7a-2, precursor              1.267835                 
hsa-let-7a-3, mature,MIMAT0000062 9859.180961                 
                                  TCGA-2G-AAGV-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 8041.494616                 
hsa-let-7a-1, mature,MIMAT0004481    7.132565                 
hsa-let-7a-2, mature,MIMAT0000062 7995.290739                 
hsa-let-7a-2, mature,MIMAT0010195   10.541048                 
hsa-let-7a-2, precursor              1.388641                 
hsa-let-7a-3, mature,MIMAT0000062 8100.448744                 
                                  TCGA-2G-AAGX-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 14120.154510                
hsa-let-7a-1, mature,MIMAT0004481    16.142226                
hsa-let-7a-2, mature,MIMAT0000062 14156.171267                
hsa-let-7a-2, mature,MIMAT0010195    52.718828                
hsa-let-7a-2, precursor               3.452383                
hsa-let-7a-3, mature,MIMAT0000062 14220.180322                
                                  TCGA-2G-AAGY-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 6193.217126                 
hsa-let-7a-1, mature,MIMAT0004481   14.458626                 
hsa-let-7a-2, mature,MIMAT0000062 6141.420291                 
hsa-let-7a-2, mature,MIMAT0010195   46.076938                 
hsa-let-7a-2, precursor              5.719896                 
hsa-let-7a-3, mature,MIMAT0000062 6207.675752                 
                                  TCGA-2G-AAGY-05A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 6483.152667                 
hsa-let-7a-1, mature,MIMAT0004481    4.028750                 
hsa-let-7a-2, mature,MIMAT0000062 6618.339583                 
hsa-let-7a-2, mature,MIMAT0010195    2.685833                 
hsa-let-7a-2, precursor              0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 6557.013067                 
                                  TCGA-2G-AAEW-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 6619.132919                 
hsa-let-7a-1, mature,MIMAT0004481    4.294653                 
hsa-let-7a-2, mature,MIMAT0000062 6651.745435                 
hsa-let-7a-2, mature,MIMAT0010195    1.744703                 
hsa-let-7a-2, precursor              0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 6705.697005                 
                                  TCGA-2G-AAEX-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 7412.830012                 
hsa-let-7a-1, mature,MIMAT0004481    3.647631                 
hsa-let-7a-2, mature,MIMAT0000062 7454.356898                 
hsa-let-7a-2, mature,MIMAT0010195    2.525284                 
hsa-let-7a-2, precursor              0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 7577.254039                 
                                  TCGA-2G-AAF1-01A-11R-A439-13
hsa-let-7a-1, mature,MIMAT0000062 7711.910036                 
hsa-let-7a-1, mature,MIMAT0004481    5.938329                 
hsa-let-7a-2, mature,MIMAT0000062 7686.786336                 
hsa-let-7a-2, mature,MIMAT0010195    1.370384                 
hsa-let-7a-2, precursor              0.000000                 
hsa-let-7a-3, mature,MIMAT0000062 7678.259505                 
                                  TCGA-2G-AAF4-01A-11R-A439-13 ⋯


In [130]:
nrow(combined_df)

[1] 977

In [127]:
nrow(other_reads)

[1] 3599

In [103]:
print(nrow(filtered_other))

[1] 947


In [ ]:
counts_combined <- merge(read_counts_teratoma, read_counts_other, by = "miRNA_ID")

# View the first few rows to check the result
head(counts_combined)

miRNA_ID     read_count_TCGA-2G-AAG5-01A-11R-A439-13
1 hsa-let-7a-1  98880                                 
2 hsa-let-7a-2  98726                                 
3 hsa-let-7a-3  99331                                 
4 hsa-let-7b   144954                                 
5 hsa-let-7c   107229                                 
6 hsa-let-7d     8058                                 
  read_count_TCGA-2G-AAG6-01A-11R-A439-13
1 199771                                 
2 199757                                 
3 202322                                 
4 257771                                 
5 326967                                 
6  11806                                 
  read_count_TCGA-2G-AAGY-05A-11R-A439-13
1 14494                                  
2 14791                                  
3 14662                                  
4 15110                                  
5  2614                                  
6   534                                  
  read_count_TCGA-2G-AAGY-01A-11R-A439-13
1 39072                                  
2 38979                                  
3 39183                                  
4 41688                                  
5 59663                                  
6  2772                                  
  read_count_TCGA-2G-AAGV-01A-11R-A439-13
1 127522                                 
2 126858                                 
3 128460                                 
4 108708                                 
5 479042                                 
6   3419                                 
  read_count_TCGA-2G-AAGX-01A-11R-A439-13
1 151508                                 
2 152317                                 
3 152572                                 
4 185933                                 
5 366449                                 
6   8887                                 
  read_count_TCGA-2G-AAFE-01A-11R-A439-13
1 40018                                  
2 39735                                  
3 40299                                  
4 41846                                  
5  6560                                  
6  1881                                  
  read_count_TCGA-2G-AAGA-01A-11R-A439-13
1 36309                                  
2 36097                                  
3 36326                                  
4 44154                                  
5 17224                                  
6  1117                                  
  read_count_TCGA-ZM-AA05-01A-12R-A43A-13 ⋯
1 62307                                   ⋯
2 61796                                   ⋯
3 62537                                   ⋯
4 49137                                   ⋯
5  5367                                   ⋯
6  4915                                   ⋯
  read_count_TCGA-WZ-A7V3-01A-11R-A43A-13
1 7584                                   
2 7509                                   
3 7638                                   
4 7979                                   
5  283                                   
6  621                                   
  read_count_TCGA-2G-AAH3-01A-11R-A439-13
1 30863                                  
2 30875                                  
3 30853                                  
4 38504                                  
5  6766                                  
6  1345                                  
  read_count_TCGA-4K-AA1I-01A-11R-A439-13
1 21545                                  
2 21129                                  
3 21440                                  
4 24463                                  
5  4421                                  
6  1168                                  
  read_count_TCGA-S6-A8JX-01A-11R-A439-13
1  7863                                  
2  8188                                  
3  8142                                  
4 17472                                  
5  3387                                  
6   388                                  
  read_count_TCGA-SO-A8JP-01A-11R-A43A-13
1 19993                          

In [133]:
write.csv(combined_df, file = "filtered_isoform_read_per_million_RNA_mapped.csv", row.names = TRUE)